In [1]:
import numpy as np
import math
import os
from os.path import isfile, join
from os import walk
import re
from pathlib import Path
import pandas as pd
import time
import scipy.io as sio
import h5py
import csv

from matplotlib import pyplot as plt
import seaborn as sns
from pandas.plotting import table
from scipy import stats

#from sklearn import datasets

# Data import 

In [2]:
root = r"C:\Users\jmccrea8\Documents\GitHub\ECE5831\Data" 
file = os.path.join(root, "Yr_data.mat")
print(Path(file).exists())# check datamount 

True


In [3]:
file = os.path.join(root, "Yr_data_1Hz.mat")
#Path(file).exists() # check datamount 

f = h5py.File(file,'r')
y_data = np.zeros( f["Yr_data"].shape)
y_data = f["Yr_data"][()]; 
#print(y_data)

file = os.path.join(root, "Xr_numeric_data_1Hz.mat")
f = h5py.File(file,'r')
x_data_ref = f["Xr_numeric"]
x_numeric_data = np.zeros([x_data_ref.shape[0], y_data.shape[1]], dtype='float32')
for j in range(0, x_data_ref.shape[0]):
    x_numeric_data[j] = f[x_data_ref[j][0]][()].astype('float32')
    #print("j: ", j, " ", x_data[j])
print(":)")

file = os.path.join(root, "Xr_catagorical_data_1Hz.mat")
f = h5py.File(file,'r')
x_data_ref = f["Xr_catagorical"]
x_catagorical_data = np.zeros([x_data_ref.shape[0], y_data.shape[1]], dtype='int8')
for j in range(0, x_data_ref.shape[0]):
    x_catagorical_data[j] = f[x_data_ref[j][0]][()].astype('int8')
    #print("j: ", j, " ", x_data[j])
print(":)")

:)
:)


In [4]:
print(x_numeric_data.shape)
print(y_data.shape)
print(x_catagorical_data.shape)

(30, 31045622)
(5, 31045622)
(15, 31045622)


In [4]:
skip = True
y_labels = list()
file = os.path.join(root, "Y_labels.csv")
with open(file) as csv_file:
    reader = csv.reader(csv_file)
    for row in reader:
        if skip :
            skip = False
        else:
            y_labels.append(row[0])

skip = True
x_numeric_labels = list()  
file = os.path.join(root, "X_numeric_labels.csv")
with open(file) as csv_file:
    reader = csv.reader(csv_file)
    for row in reader:
        if skip:
            skip = False
        else:
                x_numeric_labels.append(row[0])
x_numeric_labels[22] = "Front Right Wheel Speed" # I have it on good authority this is right, my AUTHORITY, respect it

skip = True
x_catagorical_labels = list()    
file = os.path.join(root, "X_catagorical_labels.csv")
with open(file) as csv_file:
    reader = csv.reader(csv_file)
    for row in reader:
        if skip:
            skip = False
        else:
            if "" != row[0]:
                x_catagorical_labels.append(row[0])
print(":)")

:)


## Some rudimentary feature engineering - wheel speeds not exactly the same, 

In [5]:
rear_wlr = [x_numeric_labels.index(label) for label in ['Rear Left Wheel Speed', 'Rear Right Wheel Speed' ]]
diff_rear_wslr = np.subtract(x_numeric_data[rear_wlr[0]], x_numeric_data[rear_wlr[1]])
front_wlr = [x_numeric_labels.index(label) for label in ['Front Left Wheel Speed', 'Front Right Wheel Speed']]
diff_front_wslr = np.zeros([1,x_numeric_data.shape[1]], dtype='float32')
np.subtract(x_numeric_data[front_wlr[0]],x_numeric_data[front_wlr[1]], diff_front_wslr)
diff_rear_wslr = np.zeros([1,x_numeric_data.shape[1]], dtype='float32')
np.subtract(x_numeric_data[rear_wlr[0]],x_numeric_data[rear_wlr[1]], diff_rear_wslr)
newNames = ["Front Wheel Left Right Difference", "Rear Wheel Left Right Difference"]
x_numeric_data = np.append(x_numeric_data, diff_front_wslr, axis=0)
x_numeric_data = np.append(x_numeric_data, diff_rear_wslr, axis=0)
print(len(np.unique(x_numeric_data[30])))
print(len(np.unique(x_numeric_data[31])))
{x_numeric_labels.append(name) for name in newNames}


2407
1828


{None}

In [89]:
root = r"C:\Users\jmccrea8\Documents\GitHub\ECE5831\Data" 
file = os.path.join(root, "Yr_data.npy")
np.save(file, y_data, allow_pickle=True, fix_imports=False)
file = os.path.join(root, "Yr_labels.npy")
np.save(file, y_labels, allow_pickle=True, fix_imports=False)
file = os.path.join(root, "Xr_data_cat.npy")
np.save(file, x_catagorical_data, allow_pickle=True, fix_imports=False)
file = os.path.join(root, "Xr_labels_cat.npy")
np.save(file, x_catagorical_labels, allow_pickle=True, fix_imports=False)
file = os.path.join(root, "Xr_data_num.npy")
np.save(file, x_numeric_data, allow_pickle=True, fix_imports=False)
file = os.path.join(root, "Xr_labels_num.npy")
np.save(file, x_numeric_labels, allow_pickle=True, fix_imports=False)

toDrop = ['Total Brake Torque', 'Rear Right Wheel Speed' ]
remove = [x_numeric_labels.index(label) for label in toDrop]
numeric_deleted_data = []
x_numeric_red_data = x_numeric_data
for rm in remove:
     numeric_deleted_data.append(x_numeric_data[rm])
     x_numeric_red_data = np.delete(x_numeric_data, rm, 0)
numeric_deleted_labels = {x_numeric_labels[rm] for rm in remove}
print("Stored: ", numeric_deleted_labels, "as ", np.asarray(numeric_deleted_data).shape)
x_numeric_red_labels = x_numeric_labels
{x_numeric_red_labels.pop(rm) for rm in remove}
print("Size of X numeric is: ", x_numeric_red_data.shape, ", Length of x numeric Labels is: ", len(x_numeric_red_labels))

# Exploratory Data Analysis 

In [92]:
df_cat = pd.DataFrame(x_catagorical_data.T,  columns=x_catagorical_labels) #Do a simple data import
df_num = pd.DataFrame(x_numeric_data.T, columns=x_numeric_labels) 
df_out = pd.DataFrame(y_data.T, columns = y_labels)
for col in df_cat.columns:
    df_cat[col] = df_cat[col].astype('category')

#for col in df_out.columns:
#    df_out[col] = df_out[col].astype('category')

In [93]:
file = os.path.join(root, "df_cat.pkl")
df_cat.to_pickle(file)
file = os.path.join(root, "df_num.pkl")
df_num.to_pickle(file)
file = os.path.join(root, "df_out.pkl")
df_out.to_pickle(file)

## Numerical Data
### Descriptive Stats 

In [ ]:
df_num.describe().to_csv("dfDescription.csv")

### Correlation Analysis of all numeric features

In [86]:
corr = df_num.corr(method='pearson')

In [87]:
plt.subplots(figsize=(170,90))
ax = sns.heatmap(corr, annot=True,  cmap = 'viridis', annot_kws={"size": 70})
ax.tick_params(axis='x', labelsize=80, rotation=90)
ax.tick_params(axis='y', labelsize=80)
plt.tight_layout()
plt.savefig('df_num_corr.png')

In [ ]:
|Correlation| > 0.98 against another feature: ["Front Right Wheel Speed", "Front Left Wheel Speed", "Rear Right Wheel Speed", "Rear Left Wheel Speed", "Vehicle Yaw Rate"]

### Mutual Information Calculation

In [6]:
import numpy as np
from scipy.sparse.csc import csc_matrix
from scipy import sparse
import scipy.io as sio
import time
from sys import getsizeof

import sys
sys.path.append('../') # Feeling cute might delete later
from util.mutual import MutualInfo
from util.reports import report_feature_ranking

In [9]:
binary_bias = y_data[3] > 0 
getsizeof(x_numeric_data)

3973839728

In [10]:
start = time.perf_counter()
print(np.transpose(x_numeric_data).shape)
mi = MutualInfo(np.transpose(x_numeric_data), binary_bias, 2, n_jobs=-1)
mi.compute()
end = time.perf_counter()
print('Elpased time:', end-start)

(31045622, 32)
Using parallel version
Elpased time: 221.0136476


In [11]:
mi.info

array([3.56896943e-06, 5.98328459e-04, 1.94173520e-07, 1.78481177e-02,
       1.60497985e-02, 1.38599752e-04, 1.05361051e-04, 3.79527049e-04,
       9.17837844e-06, 2.51148088e-04, 1.54060499e-03, 1.99545338e-06,
       8.55599835e-05, 4.49497791e-05, 2.68784075e-04, 1.45273838e-04,
       8.61214597e-05, 7.40517893e-04, 5.51979096e-04, 2.32748304e-04,
       7.35871576e-03, 2.34254176e-04, 2.31497693e-04, 2.24745106e-04,
       2.32790905e-04, 1.17038205e-04, 8.88107283e-05, 1.72563659e-02,
       7.04333301e-03, 8.65947913e-04, 1.23598726e-05, 8.59756847e-04])

In [81]:
mutual_out = report_feature_ranking(mi.info, x_numeric_labels, 32)

Feature ranked 1 is (CVC Control Error Angle Estimate) with value 0.017848
Feature ranked 2 is (Average Assist Torque Long Term) with value 0.017256
Feature ranked 3 is (CVC Filtered Offset Angle ) with value 0.016050
Feature ranked 4 is (Vehicle Speed Condition) with value 0.007359
Feature ranked 5 is (Average Assist Torque Short Term) with value 0.007043
Feature ranked 6 is (Steering Column Torque) with value 0.001541
Feature ranked 7 is (Pull Drift Compensation Weighted Torque) with value 0.000866
Feature ranked 8 is (Rear Wheel Left Right Difference) with value 0.000860
Feature ranked 9 is (Vehicle Yaw Rate Compensated) with value 0.000741
Feature ranked 10 is (Lateral Acceleration Condition) with value 0.000598
Feature ranked 11 is (Vehicle Yaw Rate) with value 0.000552
Feature ranked 12 is (Steering Wheel Angle Condition) with value 0.000380
Feature ranked 13 is (Vehicle Longitudinal Acceleration Compensated) with value 0.000269
Feature ranked 14 is (Compensated Steering Wheel An

## Drop features that are basically noise 

In [ ]:
low mutual information: ['Total Brake Torque', 'Vehicle Lateral Acceleration', 'Accelerator Pedal Position Percent Rate']

# Catagorical Data 

In [ ]:
#df_cat.describe().to_csv("CatDescription.csv")

### Mutual Information Calculation 

In [83]:
start = time.perf_counter()
print(np.transpose(x_catagorical_data).shape)
mi = MutualInfo(np.transpose(x_catagorical_data),binary_bias,2, n_jobs=-1)
mi.compute()
end = time.perf_counter()
print('Elpased time:', end-start)


(31045622, 32)
Using parallel version
Elpased time: 27.372442200001387


In [85]:
mutual_out = report_feature_ranking(mi.info, x_catagorical_labels, 32)

In [1]:
mi.info

NameError: name 'mi' is not defined

### Peform Chi Squared Independance test 

In [ ]:
chi_2_pvals = np.zeros([len(df_cat.columns), len(df_cat.columns)])
i = 0
j = 0 
for col in df_cat.columns: #i
    for row in df_cat.columns: #j
        if i <= j:
            print(col, row)
            contingency_table = pd.crosstab(
                df_cat[col],
                df_cat[row],
                margins = True
                )
            #f_obs = np.array([contingency_table.iloc[0:-1,-1].values,
            #                 contingency_table.iloc[-1,0:-1].values])
            chi_2_pvals[i][j] = stats.chi2_contingency(contingency_table)[1]
        j = j+1
    i = i+1
    j = 0
    
plt.subplots(figsize=(170,90))

In [ ]:
chi_2_pvals_save = chi_2_pvals
for i in range(0, chi_2_pvals.shape[0]):
    for j in range(0, chi_2_pvals.shape[1]):
        if i > j: 
            chi_2_pvals[i][j] = chi_2_pvals[j][i]
        

In [ ]:

plt.subplots(figsize=(30,40))
ax = sns.heatmap(chi_2_pvals, annot=True,  cmap = 'viridis', annot_kws={"size": 25}, xticklabels = df_cat.columns, 
                 yticklabels = df_cat.columns)
ax.tick_params(axis='x', labelsize=30, rotation=90)
ax.tick_params(axis='y', labelsize=30, rotation=60)
plt.tight_layout()

plt.savefig('df_cat_ind.png')
